## Linking a dataset of real historical persons

In this example, we deduplicate a more realistic dataset. The data is based on historical persons scraped from wikidata. Duplicate records are introduced with a variety of errors introduced.


<a target="_blank" href="https://colab.research.google.com/github/moj-analytical-services/splink/blob/master/docs/demos/examples/duckdb/deduplicate_50k_synthetic.ipynb">
  <img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/>
</a>


In [1]:
# Uncomment and run this cell if you're running in Google Colab.
# !pip install splink

### Data Setup
This pulls the data set that we'll be using in this example (it has a strong UK bias in historical figures)

In [2]:
from splink import splink_datasets

df = splink_datasets.historical_50k

downloading: https://raw.githubusercontent.com/moj-analytical-services/splink_datasets/master/data/historical_figures_with_errors_50k.parquet



…and here's a quick look at the first 10 rows of the data. Feel free to change that number to see a different number of rows, if you're running this on Colab.

In [3]:
df.head(10)

unique_id   cluster                                         full_name  \
0   Q2296770-1  Q2296770  thomas clifford, 1st baron clifford of chudleigh   
1   Q2296770-2  Q2296770                               thomas of chudleigh   
2   Q2296770-3  Q2296770               tom 1st baron clifford of chudleigh   
3   Q2296770-4  Q2296770                              thomas 1st chudleigh   
4   Q2296770-5  Q2296770              thomas clifford, 1st baron chudleigh   
5   Q2296770-6  Q2296770                      thomas clifford of chudleigh   
6   Q2296770-7  Q2296770                               tom baron chudleigh   
7   Q2296770-8  Q2296770                        tom clifford, of chudleigh   
8   Q2296770-9  Q2296770                        thomas clifford, chudleigh   
9  Q2296770-10  Q2296770                  thomas clifford, baron chudleigh   

  first_and_surname first_name    surname         dob birth_place  \
0  thomas chudleigh     thomas  chudleigh  1630-08-01       devon   
1  thomas chudleigh     thomas  chudleigh  1630-08-01       devon   
2     tom chudleigh        tom  chudleigh  1630-08-01       devon   
3  thomas chudleigh     thomas  chudleigh  1630-08-01       devon   
4  thomas chudleigh     thomas  chudleigh  1630-08-01       devon   
5  thomas chudleigh     thomas  chudleigh  1630-08-01  west devon   
6     tom chudleigh        tom  chudleigh  1630-08-01  west devon   
7     tom chudleigh        tom  chudleigh        None       devon   
8  thomas chudleigh     thomas  chudleigh  1630-05-01        None   
9  thomas chudleigh     thomas  chudleigh        None       devon   

  postcode_fake gender  occupation  
0      tq13 8df   male  politician  
1      tq13 8df   male  politician  
2      tq13 8df   male  politician  
3      tq13 8hu   None  politician  
4      tq13 8df   None  politician  
5      tq13 8df   male  politician  
6      tq13 8df   None        None  
7      tq13 8df   male  politician  
8          None   None  politician  
9      tq13 8jr   male  politician

### A quick visualization of how the data in various columns is distributed
This is used to identify which columns have skewed data (like "first_name" below) or when a particular column might have better values for measuring duplication of rows.

In [4]:
from splink import DuckDBAPI
from splink.exploratory import profile_columns

db_api = DuckDBAPI() # Splink uses DuckDB to do a lot of the analytical heavy lifting behind the scenes
profile_columns(df, db_api, column_expressions=["first_name", "substr(surname,1,2)", "gender", "occupation"]) # Shows the distribution of data in the specified columns (or parts of columns)

alt.VConcatChart(...)

### Blocking rules
This sets up blocking rules and gives a quick visualization of the relative sizes of each block. This can be helpful when determining which block might be good to use for training and which ones might be too big to help with performance.

In [5]:
from splink import DuckDBAPI, block_on
from splink.blocking_analysis import (
    cumulative_comparisons_to_be_scored_from_blocking_rules_chart,
)

blocking_rules = [
    block_on("substr(first_name,1,3)", "substr(surname,1,4)"),
    block_on("surname", "dob"),
    block_on("first_name", "dob"),
    block_on("postcode_fake", "first_name"),
    block_on("postcode_fake", "surname"),
    block_on("dob", "birth_place"),
    block_on("substr(postcode_fake,1,3)", "dob"),
    block_on("substr(postcode_fake,1,3)", "first_name"),
    block_on("substr(postcode_fake,1,3)", "surname"),
    block_on("substr(first_name,1,2)", "substr(surname,1,2)", "substr(dob,1,4)"),
]

db_api = DuckDBAPI()

cumulative_comparisons_to_be_scored_from_blocking_rules_chart(
    table_or_tables=df,
    blocking_rules=blocking_rules,
    db_api=db_api,
    link_type="dedupe_only",
)

alt.Chart(...)

### Comparisons and creating a linker (trainable model)
This sets up a list of field comparisons that we'll use as the basis for the model, uses those comparisons, along with the blocking rules created above, to build the settings for the model (linker) and then creates the linker object using those settings. This is a pretty characteristic flow for creating a Splink model.

_NOTE: there are a bunch of other tools in Splink for assessing the blocking rules and comparisons that we're omitting for the sake of simplicity in this example._

In [6]:
import splink.comparison_library as cl

from splink import Linker, SettingsCreator

# Needed to apply term frequencies to first+surname comparison
df["first_name_surname_concat"] = df["first_name"] + " " + df["surname"]

comparisons=[
    cl.ForenameSurnameComparison(
        "first_name",
        "surname",
        forename_surname_concat_col_name="first_name_surname_concat",
    ),
    cl.DateOfBirthComparison(
        "dob", input_is_string=True
    ),
    cl.PostcodeComparison("postcode_fake"),
    cl.ExactMatch("birth_place").configure(term_frequency_adjustments=True),
    cl.ExactMatch("occupation").configure(term_frequency_adjustments=True),
]


settings = SettingsCreator(
    link_type="dedupe_only",
    blocking_rules_to_generate_predictions=blocking_rules,
    comparisons=comparisons,
    retain_intermediate_calculation_columns=True,
)

linker = Linker(df, settings, db_api=db_api)

## Training the model
This is where we train the model to estimate the three sets of probabilities that drive the predictions

### Training step 1: estimate the probability of two random records being duplicates.
Just what it says on the tin. This step uses maximimum likelihood estimation to estimate the probability that two random records will be a match (are duplicates). The blocks help with the performance of the estimation process and don't have to match the blocks used in the model settings.

Note that the output, despite being in scary red, tells you what the estimated probability is and gives a nice description of what that means for the data.

In [7]:
linker.training.estimate_probability_two_random_records_match(
    [
        block_on("first_name", "surname", "dob"),
        block_on("substr(first_name,1,2)", "surname", "substr(postcode_fake,1,2)"),
        block_on("dob", "postcode_fake"),
    ],
    recall=0.6,
)

Probability two random records match is estimated to be  0.000136.
This means that amongst all possible pairwise record comparisons, one in 7,362.31 are expected to match.  With 1,279,041,753 total possible comparisons, we expect a total of around 173,728.33 matching pairs


### Training step 2: estimate the chance of a comparison being true for an UNMATCHED pair of records
This step calculates the chance that a match on a comparison will occur on records that aren't duplicated. It generates this value for each comparison (or comparison level).

The warning at the end can be ignored if it only tells you that there are missing "m" values since those will be found in the next step. It is possible that there will be missing "u" values and that's a sign that you may need to add blocks to the model in order to cover more of the data set.

In [8]:
linker.training.estimate_u_using_random_sampling(max_pairs=5e6)

----- Estimating u probabilities using random sampling -----
u probability not trained for first_name_surname - Match on reversed cols: first_name and surname (both directions) (comparison vector value: 5). This usually means the comparison level was never observed in the training data.

Estimated u probabilities using random sampling

Your model is not yet fully trained. Missing estimates for:
    - first_name_surname (some u values are not trained, no m values are trained).
    - dob (no m values are trained).
    - postcode_fake (no m values are trained).
    - birth_place (no m values are trained).
    - occupation (no m values are trained).


### Training step 3: estimate the chance of a comparison being true for an MATCHED pair of records
This is similar to step 2, but runs multiple training sessions on locally specified blocks rather than using the blocks from the model. You may need multiple training sessions to get these values across all of the comparisons in the model.

In this case, the next three cells are separate training sessions that refine these probabilities, which should be sufficient for our purposes. Look for "Your model is fully trained." at the end of the third session to make sure the process is successful.

In [9]:
training_blocking_rule = block_on("first_name", "surname")
training_session_names = (
    linker.training.estimate_parameters_using_expectation_maximisation(
        training_blocking_rule, estimate_without_term_frequencies=True
    )
)


----- Starting EM training session -----

Estimating the m probabilities of the model by blocking on:
(l."first_name" = r."first_name") AND (l."surname" = r."surname")

Parameter estimates will be made for the following comparison(s):
    - dob
    - postcode_fake
    - birth_place
    - occupation

Parameter estimates cannot be made for the following comparison(s) since they are used in the blocking rules: 
    - first_name_surname

Iteration 1: Largest change in params was 0.249 in probability_two_random_records_match
Iteration 2: Largest change in params was -0.0912 in the m_probability of postcode_fake, level `Exact match on full postcode`
Iteration 3: Largest change in params was 0.0233 in the m_probability of birth_place, level `All other comparisons`
Iteration 4: Largest change in params was -0.00959 in the m_probability of birth_place, level `Exact match on birth_place`
Iteration 5: Largest change in params was 0.00462 in the m_probability of birth_place, level `All other comp

In [10]:
training_blocking_rule = block_on("dob")
training_session_dob = (
    linker.training.estimate_parameters_using_expectation_maximisation(
        training_blocking_rule, estimate_without_term_frequencies=True
    )
)


----- Starting EM training session -----

Estimating the m probabilities of the model by blocking on:
l."dob" = r."dob"

Parameter estimates will be made for the following comparison(s):
    - first_name_surname
    - postcode_fake
    - birth_place
    - occupation

Parameter estimates cannot be made for the following comparison(s) since they are used in the blocking rules: 
    - dob

Iteration 1: Largest change in params was -0.472 in the m_probability of first_name_surname, level `Exact match on first_name_surname_concat`
Iteration 2: Largest change in params was 0.0532 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 3: Largest change in params was 0.0179 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 4: Largest change in params was 0.00552 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 5: Largest change in params was 0.00171 in the m_probability of first_name_surname, lev

### Training quality checks
The final match weights can be viewed in the match weights chart. This will show what the relative strengths of each comparison are (how strongly does it indicate duplicates or separate entities).

In [11]:
linker.visualisations.match_weights_chart()

alt.VConcatChart(...)

The unlinkables chart gives some idea of how many records can't be identified as duplicates based on how high the match score or match probability is set when doing the cluster analysis. For example, if our criteria for adding records to a cluste of duplicates is that their match weight must be above 10, about 9% of our records can't be added to a cluster because they lack sufficient information to make that determination.

In [12]:
linker.evaluation.unlinkables_chart()

alt.LayerChart(...)

## Predictions
### Predictions step 1: build pairwise predictions
This will generate a dataframe that contains scored pairs of records, allowing you to see what scores were assigned to each pair.

In [13]:
df_predict = linker.inference.predict()
df_e = df_predict.as_pandas_dataframe(limit=5)
df_e

Blocking time: 0.21 seconds
Predict time: 0.35 seconds

 -- WARNING --
You have called predict(), but there are some parameter estimates which have neither been estimated or specified in your settings dictionary.  To produce predictions the following untrained trained parameters will use default values.
Comparison: 'first_name_surname':
    u values not fully trained


match_weight  match_probability   unique_id_l  unique_id_r first_name_l  \
0     18.518207           0.999997    Q8006870-2   Q8006870-7         bill   
1      8.056298           0.996257   Q8006870-17   Q8006870-7      qilliam   
2     19.954760           0.999999   Q7787922-11   Q7787922-4          tom   
3      5.074928           0.971186  Q15432443-11  Q15432443-8        harry   
4      7.671933           0.995120  Q15432443-12  Q15432443-3         eric   

  first_name_r surname_l surname_r first_name_surname_concat_l  \
0      william   clayson   clayson                bill clayson   
1      william   clayson   clayson             qilliam clayson   
2       thomas  brodrick  brodrick                tom brodrick   
3        henry   buttler   buttler               harry buttler   
4        henry    butler    butler                 eric butler   

  first_name_surname_concat_r  ...  bf_birth_place  bf_tf_adj_birth_place  \
0             william clayson  ...      152.042739               7.740627   
1             william clayson  ...        0.165094               1.000000   
2             thomas brodrick  ...      152.042739               2.823052   
3               henry buttler  ...        0.165094               1.000000   
4                henry butler  ...        0.165094               1.000000   

   occupation_l   occupation_r  gamma_occupation  tf_occupation_l  \
0          None           None                -1              NaN   
1          None           None                -1              NaN   
2          None  naval officer                -1              NaN   
3          None           None                -1              NaN   
4          None           None                -1              NaN   

   tf_occupation_r  bf_occupation  bf_tf_adj_occupation match_key  
0              NaN            1.0                   1.0         4  
1              NaN            1.0                   1.0         4  
2         0.009451            1.0                   1.0         4  
3              NaN            1.0                   1.0         4  
4              NaN            1.0                   1.0         4  

[5 rows x 42 columns]

You can also view rows in this dataset as a waterfall chart as follows:


In [14]:
records_to_plot = df_e.to_dict(orient="records")
linker.visualisations.waterfall_chart(records_to_plot, filter_nulls=False)

alt.LayerChart(...)

### Predictions step 2: Combine the pairs into clusters
This uses the threshold_match_probability to determine which records should be combined into a cluster representing the same person. A higher threshold would result in more, smaller clusters, while a lower one could give us larger clusters with less confidence in the match.

In [15]:
clusters = linker.clustering.cluster_pairwise_predictions_at_threshold(
    df_predict, threshold_match_probability=0.95
)

Completed iteration 1, num representatives needing updating: 848
Completed iteration 2, num representatives needing updating: 202
Completed iteration 3, num representatives needing updating: 67
Completed iteration 4, num representatives needing updating: 9
Completed iteration 5, num representatives needing updating: 1
Completed iteration 6, num representatives needing updating: 0


## Model analysis
You'll need to create a "dashboards" directory if you're running this in Colab.

The following will show you a nifty visualization of the top ten clusters that result. You can hover over the nodes (=records) or the vertices/edges (=relations) to see the data they're based on or play with the threshold slider to see if your cluster breaks into separate clusters at a higher threshold

In [17]:
from IPython.display import IFrame

linker.visualisations.cluster_studio_dashboard(
    df_predict,
    clusters,
    "dashboards/50k_cluster.html",
    sampling_method="by_cluster_size",
    overwrite=True,
)


IFrame(src="./dashboards/50k_cluster.html", width="100%", height=1200)

In [18]:
linker.evaluation.accuracy_analysis_from_labels_column(
    "cluster", output_type="accuracy", match_weight_round_to_nearest=0.02
)

Blocking time: 0.35 seconds
Predict time: 0.37 seconds

 -- WARNING --
You have called predict(), but there are some parameter estimates which have neither been estimated or specified in your settings dictionary.  To produce predictions the following untrained trained parameters will use default values.
Comparison: 'first_name_surname':
    u values not fully trained


alt.LayerChart(...)

In [19]:
records = linker.evaluation.prediction_errors_from_labels_column(
    "cluster",
    threshold_match_probability=0.999,
    include_false_negatives=False,
    include_false_positives=True,
).as_record_dict()
linker.visualisations.waterfall_chart(records)

Blocking time: 0.36 seconds
Predict time: 0.11 seconds

 -- WARNING --
You have called predict(), but there are some parameter estimates which have neither been estimated or specified in your settings dictionary.  To produce predictions the following untrained trained parameters will use default values.
Comparison: 'first_name_surname':
    u values not fully trained


alt.LayerChart(...)

In [20]:
# Some of the false negatives will be because they weren't detected by the blocking rules
records = linker.evaluation.prediction_errors_from_labels_column(
    "cluster",
    threshold_match_probability=0.5,
    include_false_negatives=True,
    include_false_positives=False,
).as_record_dict(limit=50)

linker.visualisations.waterfall_chart(records)

Blocking time: 0.35 seconds
Predict time: 0.11 seconds

 -- WARNING --
You have called predict(), but there are some parameter estimates which have neither been estimated or specified in your settings dictionary.  To produce predictions the following untrained trained parameters will use default values.
Comparison: 'first_name_surname':
    u values not fully trained


alt.LayerChart(...)